In [67]:
import datetime
import fetcher
import compute
import pandas as pd
from finta import TA
import numpy as np

startDate = datetime.date(2020, 1, 1)
endDate = datetime.date(2024, 8, 10)
#endDate = datetime.date.today()
Stocks_list = []#"NVDA", "AAPL", "DKNG", "UBER"

# Retrieving tickers from a file
stocks = pd.read_csv("SCANS\\US_2024-08-10.csv")
#Neglecting tickers with Exchange values "AMEX" and "OTC"
stocks = stocks[~stocks["Exchange"].isin(["OTC", "AMEX"])]
#stocks = stocks[~stocks["Industry"].isin(["Biotechnology", "Pharmaceuticals: major", "Medical Specialties"])]
for ticker in stocks["Symbol"].tolist()[1:]:
    Stocks_list.append(ticker)

df_index = fetcher.__download_data( ["SPY"], startDate, endDate, "US")

leng = 126

focus = pd.DataFrame(columns=['ticker','ADV'])
for ticker in Stocks_list:
    
    #Neglecting tickers with .A or .B or "/" in their names
    if len(ticker.split(".")) >1 or len(ticker.split("/")) >1:
        continue
    df = fetcher.__download_data([ticker], startDate, endDate, "US")

    if len(df) < leng:
        continue
    
        
    else:
        # Avg Volume*Price
        ADV = compute.avg_dollar_vol(df, 30)
        new_row = {"ticker":ticker, "ADV": ADV}
        focus = focus.append(new_row, ignore_index=True)

   



reading from file:  yahoo_data/US/SPY2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/WES2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/EXPI2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/DAC2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/RILY2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/ML2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/SEZL2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/GES2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/CRON2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/UDMY2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/GRPN2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/WAY2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/ENFN2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/HRL2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/AVPT2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/RCUS2020-01-012024-08-10.csv


### Filtering

In [68]:
final_focus_NON_IPO = focus.loc[ (focus['ADV'] >=10000000) ]
len(final_focus_NON_IPO["ticker"].values)

2088

### Sorting by ADV

In [69]:
final_focus_NON_IPO = pd.DataFrame(final_focus_NON_IPO.sort_values(by=['ADV'], ascending=False).to_numpy(), 
                   index=final_focus_NON_IPO.index, columns=final_focus_NON_IPO.columns)

### Grouping by Sectors & Industries

In [70]:
sectors = {}
industries = {}
for index, row in final_focus_NON_IPO.iterrows():
    exchange = stocks.loc[stocks['Symbol'] == row["ticker"]]["Exchange"].values[0]
    sector = stocks.loc[stocks['Symbol'] == row["ticker"]]["Sector"].values[0]
    #print(sector)
    industry = stocks.loc[stocks['Symbol'] == row["ticker"]]["Industry"].values[0]
    #print(industry)
    if sector not in sectors.keys():
        sectors[sector] = {}
        
    if industry not in sectors[sector].keys():
        #print(industry)
        sectors[sector][industry] = []
    
    #print(sectors)
            #print(sectors[sector])
    sectors[sector][industry].append(exchange+":"+row["ticker"])

### Plotting RS line of Industries w.r.t realtive stock and comparing with the relative stock

In [74]:
import plotly.graph_objects as go
import numpy as np

for i in range(len(sectors.values())):
    for key, values in list(sectors.values())[i].items():
        if len(values)>=13:
            stocks_list = values[0:13]
        else:
            stocks_list = values
        df_index = fetcher.__download_data( ["SPY"], startDate, endDate, "US")
        df_index = df_index[-126:]

        total_marketCap = 0
        weighted_sum_close = 0
        for ticker in stocks_list:
            ticker = ticker.split(":")[1]
            #Neglecting tickers with .A or .B or "/" in their names
            if len(ticker.split(".")) >1 or len(ticker.split("/")) >1:
                continue
            df = fetcher.__download_data([ticker], startDate, endDate, "US")
            df = df[-126:]
            market_cap = stocks.loc[stocks['Symbol'] == ticker]["Market capitalization"].values[0]
            total_marketCap += market_cap   

            weighted_sum_close += market_cap*df["Close"]#[-252:0]
        weighted_sum_close /= total_marketCap
        RS = weighted_sum_close.values/df_index["Close"]

        

        # Example data
        x = list(range(0, 126)) #x = df_index["Formatted Date"] #list(range(1, 126))
        y1 = df_index["Close"]     # First line (e.g., stock price 1)
        y2 = RS    # Second line (e.g., stock price 2)

        # Select the last 20 data points for regression
        x_last_20 = x[-20:]
        y1_last_20 = y1[-20:]
        y2_last_20 = y2[-20:]

        # Perform linear regression for the last 20 points
        slope1, intercept1 = np.polyfit(x_last_20, y1_last_20, 1)
        slope2, intercept2 = np.polyfit(x_last_20, y2_last_20, 1)

        # Calculate the regression lines
        y1_regression = [slope1 * xi + intercept1 for xi in x_last_20]
        y2_regression = [slope2 * xi + intercept2 for xi in x_last_20]

        # Create the figure
        fig = go.Figure()
        """fig.update_layout({
        "plot_bgcolor" : 'black',
        "paper_bgcolor" : 'white'
        })"""
        # Add the first line (left y-axis)
        fig.add_trace(go.Scatter(
            x=x, 
            y=y1, 
            name="Relative Stock close",
            yaxis="y1",  # Bind to y-axis 1 (left)
            line=dict(color='blue')
        ))

        # Add the second line (right y-axis)
        fig.add_trace(go.Scatter(
            x=x, 
            y=y2, 
            name="RS",
            yaxis="y2",  # Bind to y-axis 2 (right)
            line=dict(color='red')
        ))

        # Add the linear regression line for y1 (left y-axis)
        fig.add_trace(go.Scatter(
            x=x_last_20, 
            y=y1_regression, 
            name="Line 1 Regression",
            yaxis="y1",  # Bind to y-axis 1 (left)
            line=dict(color='blue', dash='dash')
        ))

        # Add the linear regression line for y2 (right y-axis)
        fig.add_trace(go.Scatter(
            x=x_last_20, 
            y=y2_regression, 
            name="Line 2 Regression",
            yaxis="y2",  # Bind to y-axis 2 (right)
            line=dict(color='red', dash='dash')
        ))

        # Update layout to include both y-axes
        fig.update_layout(
            title=key,
            xaxis=dict(
                title="X-axis",
                domain=[0.1, 0.9]  # Adjusting the domain to give space for both y-axes
            ),
            yaxis=dict(
                title="Relative Stock close",
                titlefont=dict(color="blue"),
                tickfont=dict(color="blue")
            ),
            yaxis2=dict(
                title="RS",
                titlefont=dict(color="red"),
                tickfont=dict(color="red"),
                anchor="x",  # Bind this y-axis to the same x-axis
                overlaying="y",  # Overlay it on the first y-axis
                side="right"  # Position it on the right
            ),
            legend=dict(
                orientation="h",
                yanchor="bottom",
                y=1.02,
                xanchor="center",
                x=0.5
            ),
            hovermode="x unified",
            dragmode="pan",  # Enable panning with left click and drag
        )

        # Enable scroll zoom
        fig.update_layout(
            autosize=True,
        )

        # Activate scroll zooming and disable box zoom
        config = dict(
            scrollZoom=True,  # Enable zooming with mouse scroll
            displayModeBar=True,  # Show the mode bar for interactivity options
            modeBarButtonsToRemove=['zoom2d'],  # Remove the zoom box tool
        )

        # Show the figure
        fig.show(config=config)

reading from file:  yahoo_data/US/SPY2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/NVDA2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/AMD2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/AVGO2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/TSM2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/MU2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/INTC2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/QCOM2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/ARM2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/ASML2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/TXN2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/ADI2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/MRVL2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/NXPI2020-01-012024-08-10.csv


reading from file:  yahoo_data/US/SPY2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/AAPL2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/CSCO2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/MSI2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/GRMN2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/ERIC2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/CIEN2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/NOK2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/INFN2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/VSAT2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/CALX2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/HLIT2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/ARLO2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/COMM2020-01-012024-08-10.csv


reading from file:  yahoo_data/US/SPY2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/SMCI2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/DELL2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/HPQ2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/HPE2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/ZBRA2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/SONY2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/IONQ2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/NATL2020-01-012024-08-10.csv


reading from file:  yahoo_data/US/SPY2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/BA2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/RTX2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/HON2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/LMT2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/NOC2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/TDG2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/GD2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/HWM2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/LHX2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/AXON2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/SPR2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/FTAI2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/LDOS2020-01-012024-08-10.csv


reading from file:  yahoo_data/US/SPY2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/VRT2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/TER2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/PLUG2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/OLED2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/FLEX2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/VECO2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/AEHR2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/LFUS2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/VSH2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/AEIS2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/PLXS2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/PLAB2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/BHE2020-01-012024-08-10.csv


...

reading from file:  yahoo_data/US/SPY2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/WM2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/RSG2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/CLH2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/SRCL2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/GFL2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/CWST2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/PCT2020-01-012024-08-10.csv


reading from file:  yahoo_data/US/SPY2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/HAL2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/WFRD2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/FTI2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/NOV2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/LBRT2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/WHD2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/AROC2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/HLX2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/AESI2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/PUMP2020-01-012024-08-10.csv


reading from file:  yahoo_data/US/SPY2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/PWR2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/FIX2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/EME2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/BLD2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/MTZ2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/APG2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/ACM2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/FLR2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/IBP2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/TTEK2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/GVA2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/DY2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/STRL2020-01-012024-08-10.csv


reading from file:  yahoo_data/US/SPY2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/TPL2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/BXSL2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/PDI2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/OXLC2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/WT2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/STR2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/ECC2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/NEA2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/GOF2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/NZF2020-01-012024-08-10.csv


reading from file:  yahoo_data/US/SPY2020-01-012024-08-10.csv
reading from file:  yahoo_data/US/LMB2020-01-012024-08-10.csv
